# Applying Organizational Behavior to Institutions of Higher Eduction
Prepared by Wyatt Walsh (December 2020)

<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Introduction" data-toc-modified-id="Introduction-1">Introduction</a></span></li><li><span><a href="#Simulation" data-toc-modified-id="Simulation-2">Simulation</a></span></li><li><span><a href="#Data-Exploration" data-toc-modified-id="Data-Exploration-3">Data Exploration</a></span></li><li><span><a href="#Data-Modeling" data-toc-modified-id="Data-Modeling-4">Data Modeling</a></span></li><li><span><a href="#Conclusions" data-toc-modified-id="Conclusions-5">Conclusions</a></span></li></ul></div>

## Introduction

## Simulation

In [15]:
import requests
import pandas as pd
def download_file_from_google_drive(id):
    URL = "https://docs.google.com/uc?export=download"

    session = requests.Session()

    response = session.get(URL, params = { 'id' : id }, stream = True)
    token = get_confirm_token(response)

    if token:
        params = { 'id' : id, 'confirm' : token }
        response = session.get(URL, params = params, stream = True)

    return response    

def get_confirm_token(response):
    for key, value in response.cookies.items():
        if key.startswith('download_warning'):
            return value

    return None

def save_response_content(response, destination):
    CHUNK_SIZE = 32768

    with open(destination, "wb") as f:
        for chunk in response.iter_content(CHUNK_SIZE):
            if chunk: # filter out keep-alive new chunks
                f.write(chunk)
                
file_id = '1Bgu5yOMW6pyP5CKv0NW4PTqzAjQmV1_t'
download_file_from_google_drive(file_id).json()

[{'time': 1,
  'organizational_routine': [0.2383427763,
   0.230702049,
   0.307711527,
   0.2232436478],
  'organizational_routine_change': 0.5,
  'input_external_influences': [[0.4, 0.2, 0.2, 0.2],
   [0.2, 0.4, 0.2, 0.2],
   [0.2, 0.2, 0.4, 0.2],
   [0.2, 0.2, 0.2, 0.4]],
  'input_initial_routines': {'students': [[[0.7723270472,
      0.0758909843,
      0.0758909843,
      0.0758909843]],
    [[0.8111756207, 0.0629414598, 0.0629414598, 0.0629414598]],
    [[0.4082456358, 0.1972514547, 0.1972514547, 0.1972514547]],
    [[0.5976934714, 0.1341021762, 0.1341021762, 0.1341021762]],
    [[0.6373664618, 0.1208778461, 0.1208778461, 0.1208778461]],
    [[0.8858814129, 0.038039529, 0.038039529, 0.038039529]],
    [[0.8142233837, 0.0619255388, 0.0619255388, 0.0619255388]],
    [[0.3490568398, 0.2169810534, 0.2169810534, 0.2169810534]],
    [[0.828807097, 0.057064301, 0.057064301, 0.057064301]],
    [[0.2682185521, 0.2439271493, 0.2439271493, 0.2439271493]],
    [[0.6905743199, 0.1031418934, 0

In [1]:
from src import data as data
from pyspark.sql.functions import input_file_name
import os
from pyspark.sql.functions import lit
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.tuning import ParamGridBuilder
from pyspark.ml.tuning import CrossValidator
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml import Pipeline
from pyspark.sql.functions import regexp_replace
import numpy as np

In [2]:
spark = data.start_session()

In [3]:
temp = os.getcwd()
raw_data_path = temp + "/data/raw_copies/"  
df = spark.read.load(raw_data_path, format="json").withColumn("experiment", input_file_name())
df = df.withColumn('experiment', regexp_replace('experiment', 'file://' + raw_data_path + 'experiment_', ''))
df = df.withColumn('experiment', regexp_replace('experiment', '.json', ''))
df = df.join(df.select([df.input_external_influences]  + \
               [df.input_external_influences[i][j] for i in range(4) for j in range(4)]).\
        drop(df.input_external_influences)).drop(df.input_external_influences)
df = df.join(df.select([df.input_inter_group_influences	]  + \
               [df.input_inter_group_influences[i] for i in range(4)]).\
        drop(df.input_inter_group_influences)).drop(df.input_inter_group_influences)
df = df.join(df.select([df.input_opinion_flexibilities]  + \
               [df.input_opinion_flexibilities[i] for i in range(4)]).\
        drop(df.input_opinion_flexibilities)).drop(df.input_opinion_flexibilities)
df = df.join(df.select([df.input_relative_influences]  + \
               [df.input_relative_influences[i] for i in range(4)]).\
        drop(df.input_relative_influences)).drop(df.input_relative_influences)
df = df.join(df.select([df.input_renewal_frequencies]  + \
               [df.input_renewal_frequencies[0]]).\
        drop(df.input_renewal_frequencies)).drop(df.input_renewal_frequencies)
df = df.join(df.select([df.organizational_routine]  + \
               [df.organizational_routine[i] for i in range(4)]).\
            drop(df.organizational_routine)).drop(df.organizational_routine)
df = df.join(df.select([df.sd_change_faculty]  + \
               [df.sd_change_faculty[i] for i in range(4)]).\
            drop(df.sd_change_faculty)).drop(df.sd_change_faculty)
df = df.join(df.select([df.sd_change_managers]  + \
               [df.sd_change_managers[i] for i in range(4)]).\
            drop(df.sd_change_managers)).drop(df.sd_change_managers)
df = df.join(df.select([df.sd_change_other]  + \
               [df.sd_change_other[i] for i in range(4)]).\
            drop(df.sd_change_other)).drop(df.sd_change_other)
df = df.join(df.select([df.sd_change_students]  + \
               [df.sd_change_students[i] for i in range(4)]).\
            drop(df.sd_change_students)).drop(df.sd_change_students)

df = df.join(df.select([df.sd_faculty]  + \
               [df.sd_faculty[i] for i in range(4)]).\
            drop(df.sd_faculty)).drop(df.sd_faculty)
df = df.join(df.select([df.sd_managers]  + \
               [df.sd_managers[i] for i in range(4)]).\
            drop(df.sd_managers)).drop(df.sd_managers)
df = df.join(df.select([df.sd_other]  + \
               [df.sd_other[i] for i in range(4)]).\
            drop(df.sd_other)).drop(df.sd_other)
df = df.join(df.select([df.sd_students]  + \
               [df.sd_students[i] for i in range(4)]).\
            drop(df.sd_students)).drop(df.sd_students)

In [4]:
df.repartition(1).write.csv(path= temp + 'data/processed/experiment_1.csv', mode="append", header="true")

Py4JJavaError: An error occurred while calling o325.csv.
: java.lang.OutOfMemoryError: GC overhead limit exceeded
	at scala.collection.immutable.HashMap$HashTrieMap.updated0(HashMap.scala:367)
	at scala.collection.immutable.HashMap.$plus(HashMap.scala:65)
	at scala.collection.immutable.HashMap.$plus(HashMap.scala:39)
	at scala.collection.mutable.MapBuilder.$plus$eq(MapBuilder.scala:32)
	at scala.collection.mutable.MapBuilder.$plus$eq(MapBuilder.scala:28)
	at scala.collection.generic.Growable.$anonfun$$plus$plus$eq$1(Growable.scala:62)
	at scala.collection.generic.Growable$$Lambda$8/1908143486.apply(Unknown Source)
	at scala.collection.mutable.ResizableArray.foreach(ResizableArray.scala:62)
	at scala.collection.mutable.ResizableArray.foreach$(ResizableArray.scala:55)
	at scala.collection.mutable.ArrayBuffer.foreach(ArrayBuffer.scala:49)
	at scala.collection.generic.Growable.$plus$plus$eq(Growable.scala:62)
	at scala.collection.generic.Growable.$plus$plus$eq$(Growable.scala:53)
	at scala

In [23]:
train, test = df.randomSplit([0.7, 0.3], seed=18)

X = df.select(['input_negotiation_frequency', 'input_external_influences[0][0]',
 'input_external_influences[0][1]',
 'input_external_influences[0][2]',
 'input_external_influences[0][3]',
 'input_external_influences[1][0]',
 'input_external_influences[1][1]',
 'input_external_influences[1][2]',
 'input_external_influences[1][3]',
 'input_external_influences[2][0]',
 'input_external_influences[2][1]',
 'input_external_influences[2][2]',
 'input_external_influences[2][3]',
 'input_external_influences[3][0]',
 'input_external_influences[3][1]',
 'input_external_influences[3][2]',
 'input_external_influences[3][3]',
 'input_inter_group_influences[0]',
 'input_inter_group_influences[1]',
 'input_inter_group_influences[2]',
 'input_inter_group_influences[3]',
 'input_opinion_flexibilities[0]',
 'input_opinion_flexibilities[1]',
 'input_opinion_flexibilities[2]',
 'input_opinion_flexibilities[3]',
 'input_relative_influences[0]',
 'input_relative_influences[1]',
 'input_relative_influences[2]',
 'input_relative_influences[3]',
 'input_renewal_frequencies[0]',
         'time']).toPandas()
# inputs = VectorAssembler(inputCols = inputs, outputCol='features')
y = df.select([ 'organizational_routine[0]',
 'organizational_routine[1]',
 'organizational_routine[2]',
 'organizational_routine[3]']).toPandas()

Py4JJavaError: An error occurred while calling o811.collectToPython.
: java.lang.OutOfMemoryError: Java heap space


In [23]:
a = np.transpose(np.array([[1,2], 
                           [3,4],
                          [5,6],
                         [7,8]]))
b = np.array([10, 100, 1000, 10000])
# a.dot(b)
a

array([[1, 3, 5, 7],
       [2, 4, 6, 8]])

In [78]:
from glob import glob, escape
from os import makedirs, path
from pathlib import Path
import json

# Directories
root = os.getcwd()
input_dir = root + "/data/raw_0/"
output_file = root + "/data/processed/compiled.json"

# # Get array of files
# files = glob(path.join(input_dir, "**", "*.json"))
files = os.listdir(input_dir)
# glob(escape('/data/raw/*.json'))
# Data object
# data = {}

# Merge all files
for file in files:
    data.update(json.load(open(input_dir + file)))

# Create output directory
makedirs(path.dirname(output_file), exist_ok=True)

# Dump data
json.dump(data, open(output_file, "w+"))

In [28]:
import numpy as np
import pandas as pd
df_raw = pd.read_json('data/raw/experiment_1.json')
df_raw

time                             organizational_routine  \
0       1  [0.5347609325, 0.1566667756, 0.1266983941, 0.1...   
1       1  [0.49262053510000003, 0.16999400620000002, 0.1...   
2       2  [0.49262053510000003, 0.16999400620000002, 0.1...   
3       3  [0.49262053510000003, 0.16999400620000002, 0.1...   
4       4  [0.49262053510000003, 0.16999400620000002, 0.1...   
..    ...                                                ...   
96     96  [0.3633004476, 0.2126998492, 0.2026998055, 0.2...   
97     97  [0.3633004476, 0.2126998492, 0.2026998055, 0.2...   
98     98  [0.3633004476, 0.2126998492, 0.2026998055, 0.2...   
99     99  [0.3633004476, 0.2126998492, 0.2026998055, 0.2...   
100   100  [0.3633004476, 0.2126998492, 0.2026998055, 0.2...   

     organizational_routine_change  \
0                     5.000000e-01   
1                     4.214040e-02   
2                     0.000000e+00   
3                     0.000000e+00   
4                     0.000000e+00   
..                             ...   
96                    4.204000e-07   
97                    0.000000e+00   
98                    0.000000e+00   
99                    0.000000e+00   
100                   0.000000e+00   

                             input_external_influences  \
0    [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
1    [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
2    [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
3    [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
4    [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
..                                                 ...   
96   [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
97   [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
98   [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
99   [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   
100  [[0.4, 0.2, 0.2, 0.2], [0.2, 0.4, 0.2, 0.2], [...   

                                input_initial_routines  \
0    {'students': [[[0.8230436151, 0.05898546160000...   
1    {'students': [[[0.8230436151, 0.05898546160000...   
2    {'students': [[[0.8230436151, 0.05898546160000...   
3    {'students': [[[0.8230436151, 0.05898546160000...   
4    {'students': [[[0.8230436151, 0.05898546160000...   
..                                                 ...   
96   {'students': [[[0.8230436151, 0.05898546160000...   
97   {'students': [[[0.8230436151, 0.05898546160000...   
98   {'students': [[[0.8230436151, 0.05898546160000...   
99   {'students': [[[0.8230436151, 0.05898546160000...   
100  {'students': [[[0.8230436151, 0.05898546160000...   

                          input_inter_group_influences  \
0    [0.8130000000000001, 0.067, 0.0130000000000000...   
1    [0.8130000000000001, 0.067, 0.0130000000000000...   
2    [0.8130000000000001, 0.067, 0.0130000000000000...   
3    [0.8130000000000001, 0.067, 0.0130000000000000...   
4    [0.8130000000000001, 0.067, 0.0130000000000000...   
..                                                 ...   
96   [0.8130000000000001, 0.067, 0.0130000000000000...   
97   [0.8130000000000001, 0.067, 0.0130000000000000...   
98   [0.8130000000000001, 0.067, 0.0130000000000000...   
99   [0.8130000000000001, 0.067, 0.0130000000000000...   
100  [0.8130000000000001, 0.067, 0.0130000000000000...   

                          input_intra_group_influences  \
0    {'students': [[0.00494037, 0.00061487, 0.00134...   
1    {'students': [[0.00494037, 0.00061487, 0.00134...   
2    {'students': [[0.00494037, 0.00061487, 0.00134...   
3    {'students': [[0.00494037, 0.00061487, 0.00134...   
4    {'students': [[0.00494037, 0.00061487, 0.00134...   
..                                                 ...   
96   {'students': [[0.00494037, 0.00061487, 0.00134...   
97   {'students': [[0.00494037, 0.00061487, 0.00134...   
98   {'students': [[0.00494037, 0.00061487, 0.00134...   
99   {'students': [[0.00494037, 0.00061487, 0.00134...   
100  {'students': [[0.00494037, 0.00061487, 0.0013

In [16]:
df = df_raw.copy()
example_input = df['inputs'][0]
# for key in example_input.keys():
#     print(len(example_input[key]))
example_input

{'external_influences': [[0.4, 0.2, 0.2, 0.2],
  [0.2, 0.4, 0.2, 0.2],
  [0.2, 0.2, 0.4, 0.2],
  [0.2, 0.2, 0.2, 0.4]],
 'initial_routines': {'students': [[[0.8229512628000001,
     0.059016245700000004,
     0.059016245700000004,
     0.059016245700000004]],
   [[0.807875373, 0.0640415423, 0.0640415423, 0.0640415423]],
   [[0.3549169855,
     0.21502767150000002,
     0.21502767150000002,
     0.21502767150000002]],
   [[0.6491393505, 0.1169535498, 0.1169535498, 0.1169535498]],
   [[0.6638329631000001, 0.112055679, 0.112055679, 0.112055679]],
   [[0.8408500288,
     0.053049990400000004,
     0.053049990400000004,
     0.053049990400000004]],
   [[0.2834114714, 0.2388628429, 0.2388628429, 0.2388628429]],
   [[0.744718667, 0.0850937777, 0.0850937777, 0.0850937777]],
   [[0.2703688832, 0.2432103723, 0.2432103723, 0.2432103723]],
   [[0.37506860670000003, 0.2083104644, 0.2083104644, 0.2083104644]],
   [[0.6188281681000001, 0.1270572773, 0.1270572773, 0.1270572773]],
   [[0.39970189780000

In [27]:
df = df_raw.copy()
df.iloc[:, 1] = df.iloc[:, 1].apply(lambda x: np.ndarray.flatten(np.array(x)))
df.iloc[:, 2] = df.iloc[:, 2].apply(lambda x: [x[0] for x in df['decisions_group'][0][0]])

stakeholders = list(df.iloc[0,4].keys())
for i, stakeholder in enumerate(stakeholders):
    df['group_{}'.format(stakeholder)] = df['decisions_group'].apply(lambda x: x[i])
    df['group_{}_mean'.format(stakeholder)] = df['means_group'].apply(lambda x: x[stakeholder])
    df['group_{}_sd'.format(stakeholder)] = df['sd_group'].apply(lambda x: x[stakeholder])
    df['organizational_routine'] = df['organizational_routine'].apply(lambda x: np.round(x, 3))
    df['group_{}'.format(stakeholder)] = df['group_{}'.format(stakeholder)].apply(lambda x: \
                                                                            np.round(np.array(x).ravel()), 8)
    df['group_{}_mean'.format(stakeholder)] = df['group_{}_mean'.format(stakeholder)].apply(lambda x: \
                                                                            np.round(np.array(x).ravel()), 8)
    df['group_{}_sd'.format(stakeholder)] = df['group_{}_sd'.format(stakeholder)].apply(lambda x: \
                                                                            np.round(np.array(x).ravel()), 8)
    df['convergence_proportion_{}'.format(stakeholder)] = df['convergence_proportions_group'].apply(lambda x: \
                                                                                                   x[stakeholder])
df = df.drop(['decisions_group', 'means_group', 'sd_group', 'convergence_proportions_group'], 1)
# # pd.DataFrame(data = list(external.values())[0], columns = external.keys())
# df['group_students'] = df.iloc[:, 2].apply(lambda x: [x]
df

inputs  \
0    {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
1    {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
2    {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
3    {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
4    {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
..                                                 ...   
96   {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
97   {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
98   {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
99   {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   
100  {'external_influences': [[0.4, 0.2, 0.2, 0.2],...   

           organizational_routine  time        group_students  \
0    [0.235, 0.257, 0.274, 0.234]     1  [1.0, 0.0, 0.0, 0.0]   
1    [0.243, 0.264, 0.252, 0.241]     1  [1.0, 0.0, 0.0, 0.0]   
2    [0.246, 0.266, 0.243, 0.245]     2  [1.0, 0.0, 0.0, 0.0]   
3     [0.248, 0.265, 0.24, 0.247]     3  [1.0, 0.0, 0.0, 0.0]   
4     [0.249, 0.264, 0.24, 0.247]     4  [1.0, 0.0, 0.0, 0.0]   
..                            ...   ...                   ...   
96   [0.248, 0.248, 0.257, 0.248]    96  [1.0, 0.0, 0.0, 0.0]   
97   [0.248, 0.248, 0.257, 0.248]    97  [1.0, 0.0, 0.0, 0.0]   
98   [0.248, 0.248, 0.257, 0.248]    98  [1.0, 0.0, 0.0, 0.0]   
99   [0.248, 0.248, 0.257, 0.248]    99  [1.0, 0.0, 0.0, 0.0]   
100  [0.248, 0.248, 0.257, 0.248]   100  [1.0, 0.0, 0.0, 0.0]   

      group_students_mean     group_students_sd  \
0    [1.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
1    [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
2    [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
3    [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
4    [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
..                    ...                   ...   
96   [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
97   [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
98   [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
99   [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
100  [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   

     convergence_proportion_students         group_faculty  \
0                           0.000000  [0.0, 1.0, 0.0, 0.0]   
1                           0.272131  [0.0, 1.0, 0.0, 0.0]   
2                           0.016393  [0.0, 1.0, 0.0, 0.0]   
3                           0.000000  [0.0, 1.0, 0.0, 0.0]   
4                           0.000000  [0.0, 1.0, 0.0, 0.0]   
..                               ...                   ...   
96                          0.000000  [0.0, 1.0, 0.0, 0.0]   
97                          0.000000  [0.0, 1.0, 0.0, 0.0]   
98                          0.000000  [0.0, 1.0, 0.0, 0.0]   
99                          0.000000  [0.0, 1.0, 0.0, 0.0]   
100                         0.000000  [0.0, 1.0, 0.0, 0.0]   

       group_faculty_mean      group_faculty_sd  \
0    [0.0, 1.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
1    [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
2    [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
3    [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
4    [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
..                    ...                   ...   
96   [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
97   [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
98   [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
99   [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   
100  [0.0, 0.0, 0.0, 0.0]  [0.0, 0.0, 0.0, 0.0]   

     convergence_proportion_faculty        group_managers  \
0                              0.00  [0.0, 0.0, 1.0, 0.0]   
1                              0.12  [0.0, 0.0, 1.0, 0.0]   
2                              0.08  [0.0, 0.0, 1.0, 0.0]   
3                              0.08  [0.0, 0.0, 1.0, 0.0]   
4                              0.12  [0.0, 0.0, 1.0, 0.0]   
..                              ...                   ...   
96                             1.00  [0.0, 0.0, 1.0, 0.0]   
97                             1.00  [0.0, 0.0, 1.0, 0.0]   
98                             1.00  [0.0, 0.0, 1.

In [10]:
df['inputs'][0]

{'external_influences': [[0.4, 0.2, 0.2, 0.2],
  [0.2, 0.4, 0.2, 0.2],
  [0.2, 0.2, 0.4, 0.2],
  [0.2, 0.2, 0.2, 0.4]],
 'initial_routines': {'students': [[[0.7899021744,
     0.0700326085,
     0.0700326085,
     0.0700326085]],
   [[0.35709844420000003,
     0.21430051860000002,
     0.21430051860000002,
     0.21430051860000002]],
   [[0.807764154, 0.0640786153, 0.0640786153, 0.0640786153]],
   [[0.5826962882, 0.1391012373, 0.1391012373, 0.1391012373]],
   [[0.5950770549000001, 0.134974315, 0.134974315, 0.134974315]],
   [[0.9670201672000001, 0.0109932776, 0.0109932776, 0.0109932776]],
   [[0.9400562901, 0.0199812366, 0.0199812366, 0.0199812366]],
   [[0.7088593887, 0.0970468704, 0.0970468704, 0.0970468704]],
   [[0.6493934690000001, 0.1168688437, 0.1168688437, 0.1168688437]],
   [[0.2522106462, 0.2492631179, 0.2492631179, 0.2492631179]],
   [[0.8440417153, 0.0519860949, 0.0519860949, 0.0519860949]],
   [[0.9970002752, 0.0009999083, 0.0009999083, 0.0009999083]],
   [[0.8289503196, 0

In [118]:
opinion_flexibilities = [[0.2, 0.2, 0.2, 0.2],
								[0.5, 0.5, 0.5, 0.5],
		                        [0.8, 0.8, 0.8, 0.8],
		                        [np.ones((10,4)).apply(lambda)]
opinion_flexibilities


ValueError: too many values to unpack (expected 4)

In [1]:
from src import model as model 

model = model.Model()
stakeholders = [['students', 'faculty', 'managers', 'other']]
number_of_agents = [[1830, 150, 30, 240]]
negotiation_frequency = [1]
model.generate_experiment_parameter_set(stakeholders, number_of_agents, negotiation_frequency)
time_steps_per_experiment = 500
model.set_environment(model.experiment_parameters[0])
model.run_experiment(1, time_steps_per_experiment)

ModuleNotFoundError: No module named 'environment'

In [ ]:
model.environment.agents['students'][0].inertial_clock

In [19]:
[item['relative_influences'] for item in model.experiment_parameters]

[[0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.013, 0.107],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.25, 0.25, 0.25, 0.25],
 [0.813, 0.067, 0.013, 0.107],
 [0.813, 0.067, 0.

In [2]:
random.seed(18)
stakeholders = ['Students', 'Faculty', 'Administration', 'Other Internal']
intergroup_influences = [[0.2], [0.3], [0.4], [0.1]]
negotiation_frequency = 1
# number of agents, renewal_frequency, group_influence, opinion_flexibility, 
# initial_routine, external_influence, influence_proportions

renewal_frequency = [5, 3, 2, 4]
random_vars = [np.random.uniform(0,1,x) for x in number_of_agents]
intragroup_influences = [[x/sum(y) for x in y] for y in random_vars]
opinion_flexibility = [0.75, 0.45, 0.25, 0.2]
initial_routine = [[1,0,0,0]] + \
                [[0,1,0,0]] + \
                [[0,0,1,0]] + \
                [[0,0,0,1]]
external_influence = [0.25, 0.25, 0.25, 0.25]
influence_proportions = [[0.25, 0.3 , 0.25 , 0.15 , 0.05]] + \
                        [[0.25, 0.2 , 0.3 , 0.225 , 0.075]] + \
                        [[0.25, 0.05 , 0.2 , 0.4 , 0.1]] + \
                        [[0.25, 0.05, 0.2 , 0.2 , 0.3]]
agents_dictionary = {
    'Students': [number_of_agents[0], renewal_frequency[0], 
                 opinion_flexibility[0], initial_routine[0], external_influence, influence_proportions[0]],
    'Faculty': [number_of_agents[1], renewal_frequency[1], 
                 opinion_flexibility[1], initial_routine[1], external_influence, influence_proportions[1]],
    'Administration': [number_of_agents[2], renewal_frequency[2], 
                 opinion_flexibility[2], initial_routine[2], external_influence, influence_proportions[2]],
    'Other': [number_of_agents[3], renewal_frequency[3], 
                 opinion_flexibility[3], initial_routine[3], external_influence, influence_proportions[3]]
}

In [16]:

from src import model as model 
from src import utilities as utils
from sklearn.model_selection import ParameterGrid as grid
import numpy as np

model = model.Model()

model.stakeholders = ['students', 'faculty', 'managers', 'other']
model.
model.negotiation_frequency = 1
for i, stakeholder in enumerate(model.stakeholders):
    rvs = np.random.default_rng().exponential(scale = 1, size = model.number_of_agents[i]).tolist()
    rvs_normal = utils.normalize(rvs)
    model.intra_group_influences[stakeholder] = rvs_normal




intergroup_influences = [
						[0.1, 0.1, 0.7, 0.1],
						[0.2, 0.2, 0.4, 0.2],
						[0.813, 0.067, 0.013, 0.107]
						]

renewal_frequencies = [
					[1, 1, 1, 1],
					[5, 5, 5, 5],
					[10, 10, 10, 10]
					]

initial_routines_all = []
initial_routines = {}
for i, stakeholder in enumerate(model.stakeholders):
	  initial_list = [0]*len(model.stakeholders) 
	  initial_list[i] = 1
	  initial_routines[stakeholder] = [initial_list] * model.number_of_agents[i]
initial_routines_all += [initial_routines]
initial_routines = {}
for i, stakeholder in enumerate(model.stakeholders):
	rvs = np.random.default_rng().uniform(low = 0.25, high = 1, size = model.number_of_agents[i])
	routine_proportion_other = np.round((1 - rvs)/3,3)
	routines = [[a, b, b, b] for a,b in zip(rvs, routine_proportion_other)]
	rvs_normal = [[utils.normalize(x)] for x in routines]
	intial_routines[stakeholder] = rvs_normal
initial_routines_all += [initial_routines]

model.external_influences = initial_routines_all[0]

relative_influences = [
					[0.25, 0.25, 0.25, 0.25],
					[0.813, 0.067, 0.013, 0.107]
					]

param_grid = {
    'inter_group_influences': intergroup_influences,
    'renewal_frequencies': renewal_frequencies,
    'initial_routines': initial_routines_all,
    'relative_influences': relative_influences
}
a = grid(param_grid)

In [ ]:
'opinion_flexibilities': opinion_flexibilities,
    opinion_flexibility_influence_dependent = (1 - np.array(model.inter_group_influences)).tolist()
opinion_flexibilities = 


In [53]:
params = []
for i, combo in enumerate(a):
    keys = [*combo]
    values = [[a] for a in combo.values()]
    b = dict(zip(keys, values))
    b['opinion_flexibilities'] = [[0.2, 0.2, 0.2, 0.2],
                                        [0.8, 0.8, 0.8, 0.8],
                                    [np.round((1 - np.array(combo['inter_group_influences'])),3).tolist()]
                                          ]
    c = grid(b)
    params += c
#     a[i]['opinion'] = {'opinion_flexibilities': [[0.2, 0.2, 0.2, 0.2],
#                                         [0.8, 0.8, 0.8, 0.8],
#                                     [(1 - np.array(combo['inter_group_influences'])).tolist()]
#                                           ]}
#     break

In [55]:
params

[{'initial_routines': {'students': [[1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 0],
    [1, 0, 0, 

In [167]:
abs(0)

0

In [6]:
np.shape(model.data['Time Evolving Parameters']['Organizational Routine'])

(101, 1, 4, 1, 1)

In [2]:
random.seed(18)
#  num_agents, choice_frequency, group_influence, change_capacity, feedback_proximity
agents_dictionary = {
    'Students': [1000, 5, 1/1000, 20, 0.8, 50, 20, 50, 30],
    'Faculty': [200, 2, 1/200, 10, 0.4, 50, 10, 50, 30],
    'Administration':[50, 1, 1/50, 5, 0.1, 50, 5, 50, 10],
    'Staff': [100, 3, 1/100, 15, 0.2, 50,10,50,20]
}

influences_between_groups = [0.08,0.3,0.6, 0.02]

environment = env.Environment(50, influences_between_groups, 5)
environment.add_agents(agents_dictionary)
environment.simulate(500)

In [3]:
environment.data

{'Organizational Routine': [[50],
  49.93773122459372,
  50.23663122459371,
  50.53553122459372,
  50.83443122459373,
  51.13333122459373,
  51.43223122459374,
  51.73113122459372,
  52.03003122459372,
  52.32893122459373,
  52.62783122459374,
  52.92673122459375,
  53.225631224593734,
  53.524531224593716,
  53.82343122459368,
  54.12233122459366,
  54.42123122459364,
  54.72013122459363,
  55.019031224593625,
  55.31793122459363,
  55.61683122459362,
  55.915731224593635,
  56.21463122459363,
  56.513531224593706,
  56.81243122459373,
  57.111331224593705,
  57.41023122459376,
  57.70913122459374,
  58.00803122459375,
  58.30693122459376,
  58.605831224593686,
  58.90473122459368,
  59.20363122459367,
  59.50253122459368,
  59.80143122459368,
  60.100331224593674,
  60.399231224593684,
  60.69813122459366,
  60.99703122459367,
  61.295931224593666,
  61.59483122459365,
  61.89373122459368,
  62.19263122459365,
  62.49153122459364,
  62.79043122459367,
  63.08933122459364,
  63.388231

## Data Exploration

## Data Modeling 

## Conclusions